In [10]:
import pandas as pd
from sentence_transformers import SentenceTransformer, util
from torch import load, Tensor, save
import pickle

In [11]:
file_path = "data/firefox_samples.pkl"
with open(file_path, 'rb') as f:
    samples_reports = pickle.load(f)

In [12]:
samples_reports[1]["reports"]

description  \
bug_id                                                      
237798  User-Agent:       Mozilla/5.0 (X11; U; Linux i...   
432630  User-Agent:       Mozilla/5.0 (Windows; U; Win...   
281332  User-Agent:       Mozilla/5.0 (Windows; U; Win...   
244614  User-Agent:       Mozilla/5.0 (Windows; U; Win...   
225530  User-Agent:       Mozilla/5.0 (Windows; U; Win...   
...                                                   ...   
264533  User-Agent:       Mozilla/5.0 (Windows; U; Win...   
233724  User-Agent:       ; Build Identifier: Mozilla/...   
293919  User-Agent:       Mozilla/5.0 (Windows; U; Win...   
294866  User-Agent:       Mozilla/5.0 (Windows; U; Win...   
582853  User-Agent:       Mozilla/5.0 (Windows; Window...   

                                               short_desc  
bug_id                                                     
237798  Firefox unresponsive while parsing large XML File  
432630  about:livemark-failed is not a valid URL but i...  
281332  any address typed in with two colons after the...  
244614                 Wrong symbols in bookmark-toolbar.  
225530  Find in this page does not work in installer v...  
...                                                   ...  
264533  If an url doesnt contains colon after http; br...  
233724  firefox for solaris (using Suns build) crashes...  
293919             Crash when open a html/javascript page  
294866               cropped panels and improper resizing  
582853        Close Minimize and Maximize buttons missing  

[436 rows x 2 columns]

In [13]:
# model = SentenceTransformer("all-mpnet-base-v2")
model = SentenceTransformer("luiz-and-robert-thesis/all-mpnet-base-v2-lr-1e-8-margin-5-epoch-3")

In [14]:
sample_encodings = {}

for key, value in samples_reports.items():
    encoded_desc = []
    report_id_list = []
    for index, row in value["reports"].iterrows():
        try:
            text = f"{row['short_desc']} - {row['description']}"
            encoded = model.encode(text)
        except:
            encoded = None
        
        report_id = index
        encoded_desc.append(encoded)
        report_id_list.append(report_id)
    
    dataset_encoded_df = pd.DataFrame()
    dataset_encoded_df["encoded_desc"] = encoded_desc
    dataset_encoded_df["bug_id"] = report_id_list
    dataset_encoded_df = dataset_encoded_df.set_index('bug_id')
    enc_dict = dataset_encoded_df.to_dict()

    sample_encodings[key] = enc_dict['encoded_desc']

    

In [6]:
sample_encodings[1]

{237798: array([-1.00122085e-02, -1.39024006e-02, -1.74806640e-02, -9.64029133e-03,
         6.84011579e-02, -5.90343727e-03, -3.07564735e-02,  7.93242157e-02,
         8.03972185e-02, -2.51880512e-02, -1.97422616e-02, -1.29975183e-02,
         4.52772807e-03, -1.41401701e-02, -6.08565770e-02, -7.68323941e-03,
         1.45574077e-03, -3.08266003e-02,  3.84778976e-02, -3.32546346e-02,
        -2.34553893e-03, -3.02363858e-02,  4.82535660e-02, -8.23077280e-03,
        -4.06343229e-02, -9.38106049e-03,  2.65034828e-02, -8.85035098e-03,
        -3.14674601e-02, -4.05464806e-02,  1.73988577e-03,  1.43155549e-02,
        -9.01945308e-02,  8.50686803e-02,  1.98644739e-06, -2.77430452e-02,
         4.65418138e-02,  3.20488177e-02, -4.81530296e-05,  7.35946298e-02,
        -2.62931250e-02, -6.71999482e-03, -6.00940324e-02, -9.77023318e-03,
         3.84008586e-02,  1.17454049e-03, -5.35688326e-02, -2.28554010e-02,
        -1.55071751e-03, -1.57332793e-02, -5.53338369e-03, -3.96471955e-02,
    

In [18]:
type(sample_encodings[1][582853])

numpy.ndarray

In [20]:
util.cos_sim(sample_encodings[1][582853], sample_encodings[1][293919])

tensor([[0.1400]])

In [17]:
file_path = "data/encodings/fine-tuned-models/mpnet-lr-1e-8-m-5-e-3/mpnet-lr-1e-8-m-5-e-3-firefox-encodings-samples.pkl"

with open(file_path, 'wb') as f:
    pickle.dump(sample_encodings, f)